In [16]:
import scanpy as sc 
import numpy as np  
import pickle as pkl
import gzip
import anndata
from pathlib import Path
import sys
from tqdm import tqdm
import pickle
#sys.path.insert(1, str('ondemand/data/sys/lscm/bin/Geneformer'))
import anndata as ad
import scipy.sparse as sp
import pandas as pd
## geneformer imports
from geneformer import TranscriptomeTokenizer, EmbExtractor, InSilicoPerturber, InSilicoPerturberStats

In [2]:
## Define paths

d_path = '/data/scratch/bty416/scFMs/data'
raw_expr_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts'

### Norman dataset

#### Control data

In [5]:
## Load files for Norman data, including mask and check shape

with open(f'{raw_expr_path}/norman_mask_df.pkl', 'rb') as f:
    norman_cl_mask = pkl.load(f)
    
norman_ctrl_adata = sc.read_h5ad(f'{raw_expr_path}/norman/ctrl_norman_raw_counts.h5ad')

print(f'Mask shape: {norman_cl_mask.shape}, adata shape: {norman_ctrl_adata.shape}')

Mask shape: (11855, 102), adata shape: (11855, 21265)


In [12]:
def gf_preprocess(data_directory, output_directory):
    
    ctrl_adata = sc.read_h5ad(data_directory)
    
    if 'ensembl_id' not in ctrl_adata.var:
    ## Rename columns for tokenizer to function correctly
        ctrl_adata.var['ensembl_id'] = ctrl_adata.var_names
    
    if 'ncounts' in ctrl_adata.var:
        ctrl_adata.var.rename(columns={'ncounts': 'n_counts'}, inplace=True)
    
    else: 
        ctrl_adata.obs.rename(columns={'read_count': 'n_counts'}, inplace=True)
    
    ctrl_adata.write_h5ad(output_directory)
    
    return ctrl_adata

In [10]:
norman_ctrl_adata = gf_preprocess(f'{raw_expr_path}/norman/ctrl_norman_raw_counts.h5ad', f'{raw_expr_path}/tokenizer_input/ctrl_norman_raw_counts.h5ad')

In [13]:
def gf_tokenizer(data_directory: str, output_path: str):
    
    tk = TranscriptomeTokenizer(nproc=16)
    
    tokenized_cells, cell_metadata = tk.tokenize_anndata(str(data_directory))
    
    tokenized_dataset = tk.create_dataset(tokenized_cells, cell_metadata)
    
    tokenized_dataset.save_to_disk(output_path)
    
    print(f'Saved tokenized_dataset to {output_path}')
    
    return tokenized_dataset

In [40]:
norman_directory = str(Path(f'{raw_expr_path}/tokenizer_input/ctrl_norman_raw_counts.h5ad').resolve())
output_directory = Path(f'{d_path}/tokenized_data/').resolve()
norman_prefix = "norman"
norman_output_path = str((Path(output_directory) / norman_prefix).with_suffix(".dataset"))

norman_token = gf_tokenizer(norman_directory, norman_output_path)

/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/anndata/__init__.py:55: FutureWarning: `anndata.read` is deprecated, use `anndata.read_h5ad` instead. `ad.read` will be removed in mid 2024.
  warnings.warn(
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:231: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:234: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_mi

/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/ctrl_norman_raw_counts.h5ad has no column attribute 'filter_pass'; tokenizing all cells.
Creating dataset.


Saving the dataset (1/1 shards): 100%|██████████| 11855/11855 [00:00<00:00, 202354.15 examples/s]

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/norman.dataset


In [14]:
def gf_extract_ctrl_embs(emb_mode: str = 'cell', batch_size: int = 64, dataset: str = 'norman'):
    
    # initiate EmbExtractor
    embex = EmbExtractor(model_type="Pretrained",
                         num_classes=0,
                         emb_mode=emb_mode,
                         emb_layer=0,
                         max_ncells=20000,
                         forward_batch_size=batch_size,
                         nproc=16)

    # extracts embedding from input data
    # input data is tokenized rank value encodings generated by Geneformer tokenizer (see tokenizing_scRNAseq_data.ipynb)
    # example dataset: https://huggingface.co/datasets/ctheodoris/Genecorpus-30M/tree/main/example_input_files/cell_classification/disease_classification/human_dcm_hcm_nf.dataset
    embs = embex.extract_embs("../bin/Geneformer",
                              f"{d_path}/tokenized_data/{dataset}.dataset",
                              f"{d_path}/embeddings/",
                              f"{dataset}_ctrl_{emb_mode}")
    
    embs.to_pickle(f"{d_path}/embeddings/{dataset}_ctrl_{emb_mode}.pkl.gz", compression="gzip")
    
    return embs

In [12]:
norman_ctrl_cell = gf_extract_ctrl_embs()

100%|██████████| 186/186 [00:45<00:00,  4.10it/s]


***
#### Perturbation data

In [13]:
## Load data

with open(f'{raw_expr_path}/norman/all_perts.pkl', 'rb') as f:
    norman_all_perts = pkl.load(f)

In [14]:
## Find perturbations in control data
len(set(norman_ctrl_adata.var['gene_symbols']).intersection(norman_all_perts))

102

In [15]:
## Find non expressed genes
non_exp_gene = norman_cl_mask.columns[norman_cl_mask.sum() == 0]

In [45]:
def prep_pert_data(all_perts, mask, adata, save_path):
    
    non_exp_genes = mask.columns[mask.sum() == 0]
    
    for pert in tqdm(all_perts):
        
        if pert in non_exp_genes:
            pass
        
        elif Path(f'{save_path}/{pert}_slice.h5ad').is_file():
            print(f'{pert} adata already prepared.')
        
        else:
            try:
                cell_mask = mask[pert].values

                if 'gene_symbols' in adata.var:
                    gene_mask = adata.var['gene_symbols'] != pert

                else:
                    gene_mask = adata.var_names != pert

                sliced_adata = adata[cell_mask, gene_mask]

                assert sliced_adata.shape[1] == adata.shape[1] - 1

                sliced_adata.write_h5ad(f'{save_path}/{pert}_slice.h5ad')
            
            except KeyError as ke:
                print('Key not found in mask:', ke)
                pass

In [234]:
norman_pert_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/norman'

prep_pert_data(norman_all_perts, norman_cl_mask, norman_ctrl_adata, norman_pert_path)

100%|██████████| 102/102 [00:00<00:00, 890.05it/s]

FOXO4 adata already prepared.
HOXA13 adata already prepared.
CSRNP1 adata already prepared.
FOXA1 adata already prepared.
DUSP9 adata already prepared.
SLC4A1 adata already prepared.
MAP2K6 adata already prepared.
KMT2A adata already prepared.
LHX1 adata already prepared.
CKS1B adata already prepared.
NIT1 adata already prepared.
MAP2K3 adata already prepared.
HOXB9 adata already prepared.
ZBTB1 adata already prepared.
JUN adata already prepared.
UBASH3B adata already prepared.
CDKN1A adata already prepared.
NCL adata already prepared.
IKZF3 adata already prepared.
FOXF1 adata already prepared.
FOXA3 adata already prepared.
CNNM4 adata already prepared.
HK2 adata already prepared.
FOXL2 adata already prepared.
RHOXF2 adata already prepared.
EGR1 adata already prepared.
HOXC13 adata already prepared.
ZNF318 adata already prepared.
PRDM1 adata already prepared.
S1PR2 adata already prepared.
CBFA2T3 adata already prepared.
SPI1 adata already prepared.
HNF4A adata already prepared.
FEV ada

In [16]:
def tokenize_pert_data(all_perts, non_exp_genes, input_dir, output_dir):
        
    for pert in tqdm(all_perts):
        
        if pert in non_exp_genes:
            pass
        
        else:
            in_dir = f'{input_dir}/{pert}_slice.h5ad'
            prefix = f'{pert}'
            out_path = (Path(output_dir) / prefix).with_suffix(".dataset")

            if out_path.is_dir():
                print(f'{out_path} already exists {pert} adata already tokenized.')
            
            else: 
                tokenized = gf_tokenizer(in_dir, str(out_path))

In [50]:
norman_pert_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/norman'
tokenized_dir = '/data/scratch/bty416/scFMs/data/tokenized_data'

non_exp_gene = norman_cl_mask.columns[norman_cl_mask.sum() == 0]

tokenize_pert_data(norman_all_perts, non_exp_gene, norman_pert_path, tokenized_dir)

  0%|          | 0/102 [00:00<?, ?it/s]

/data/scratch/bty416/scFMs/data/tokenized_data/FOXO4.dataset already exists FOXO4 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/HOXA13.dataset already exists HOXA13 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/CSRNP1.dataset already exists CSRNP1 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/FOXA1.dataset already exists FOXA1 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/DUSP9.dataset already exists DUSP9 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/SLC4A1.dataset already exists SLC4A1 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/MAP2K6.dataset already exists MAP2K6 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/KMT2A.dataset already exists KMT2A adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/LHX1.dataset already exists LHX1 adata already tokenized.
/data/scratch/bty416/scFMs/data

/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:231: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:234: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/norman/IRF1_slice.h5ad has no column attribute 'filter_pass'; tokenizing all cells.
Creating dataset.



Map (num_proc=16): 100%|██████████| 500/500 [00:21<00:00, 23.72 examples/s]

 46%|████▌     | 47/102 [00:23<00:27,  1.97it/s]/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/anndata/__init__.py:55: FutureWarning: `anndata.read` is deprecated, use `anndata.read_h5ad` instead. `ad.read` will be removed in mid 2024.
  warnings.warn(
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:231: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:234: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with 

...

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/SGK1.dataset
/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/norman/HES7_slice.h5ad has no column attribute 'filter_pass'; tokenizing all cells.
Creating dataset.



Map (num_proc=16): 100%|██████████| 26/26 [00:18<00:00,  1.42 examples/s]

 99%|█████████▉| 101/102 [20:29<00:21, 21.66s/it]/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/anndata/__init__.py:55: FutureWarning: `anndata.read` is deprecated, use `anndata.read_h5ad` instead. `ad.read` will be removed in mid 2024.
  warnings.warn(
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:231: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/data/scratch/bty416/lscm/geneformer_venv/lib/python3.10/site-packages/geneformer/tokenizer.py:234: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with D

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/HES7.dataset
/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/norman/MEIS1_slice.h5ad has no column attribute 'filter_pass'; tokenizing all cells.
Creating dataset.



Map (num_proc=16): 100%|██████████| 476/476 [00:20<00:00, 23.46 examples/s]

100%|██████████| 102/102 [20:52<00:00, 12.28s/it]

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/MEIS1.dataset


In [17]:
def embed_pert_data(all_perts, all_perts_embex, non_exp_genes, token_dir, output_dir, 
                    emb_mode: str = 'cell', batch_size: int = 64, dataset: str = 'norman'):
    
    for pert in all_perts:
        
        if pert in non_exp_genes:
            pass
        
        else:
            
            # initiate EmbExtractor
            embex = EmbExtractor(model_type="Pretrained",
                                 num_classes=0,
                                 emb_mode=emb_mode,
                                 emb_layer=0,
                                 max_ncells=20000,
                                 forward_batch_size=batch_size,
                                 nproc=16)

            # extracts embedding from input data
            # input data is tokenized rank value encodings generated by Geneformer tokenizer (see tokenizing_scRNAseq_data.ipynb)
            # example dataset: https://huggingface.co/datasets/ctheodoris/Genecorpus-30M/tree/main/example_input_files/cell_classification/disease_classification/human_dcm_hcm_nf.dataset
            embs = embex.extract_embs("../bin/Geneformer",
                                      f"{d_path}/tokenized_data/{pert}.dataset",
                                      output_dir,
                                      f"{pert}_pert_{emb_mode}")
            
            all_perts_embex[pert] = embs
    
    with gzip.open(f"{d_path}/embeddings/{dataset}_perts_{emb_mode}.pkl.gz", 'wb') as f:
        
        pkl.dump(all_perts_embex, f)
        
    print(f'all_perts_embex saved to {d_path}/embeddings/{dataset}_perts_{emb_mode}.pkl.gz')
        
    return all_perts_embex

In [61]:
all_perts_embex = {}
non_exp_genes = norman_cl_mask.columns[norman_cl_mask.sum() == 0]

tokenized_dir = '/data/scratch/bty416/scFMs/data/tokenized_data'
out_dir = f"{d_path}/embeddings/"

all_perts_embex = embed_pert_data(norman_all_perts, all_perts_embex, non_exp_genes, tokenized_dir, out_dir,dataset='norman')

100%|██████████| 8/8 [00:01<00:00,  4.85it/s]


In [62]:
for emb in all_perts_embex.values():
    print(emb.shape)

(500, 256)
(3, 256)
(500, 256)
(94, 256)
(500, 256)
(92, 256)
(5, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(111, 256)
(500, 256)
(500, 256)
(8, 256)
(500, 256)
(334, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(292, 256)
(500, 256)
(500, 256)
(500, 256)
(7, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(425, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(158, 256)
(500, 256)
(416, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(78, 256)
(500, 256)
(500, 256)
(43, 256)
(500, 256)
(500, 256)
(271, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(104, 256)
(10, 256)
(27, 256)
(500, 256)
(47, 256)
(38, 256)
(500, 256)
(500, 256)
(189

***
### Replogle datasets
#### Control cells

In [14]:
## Load files for RPE1 data, including mask and check shape

with open(f'{raw_expr_path}/replogle_rpe1_mask_df.pkl', 'rb') as f:
    rpe1_mask = pkl.load(f)
    
rpe1_adata = sc.read_h5ad(f'{raw_expr_path}/replogle_rpe1/replogle_rpe1_raw_counts.h5ad')

print(f'Mask shape: {rpe1_mask.shape}, adata shape: {rpe1_adata.shape}')

## Filter for control cells and check shape
rpe1_ctrl_adata = rpe1_adata[rpe1_adata.obs['perturbation'] == 'control', :]

print(f'adata shape: {rpe1_ctrl_adata.shape}')

KeyboardInterrupt: 

In [ ]:
## Load files for K562 data, including mask and check shape

with open(f'{raw_expr_path}/replogle_k562_mask_df.pkl', 'rb') as f:
    k562_mask = pkl.load(f)
    
k562_adata = sc.read_h5ad(f'{raw_expr_path}/replogle_k562/replogle_k562_raw_counts.h5ad')

print(f'Mask shape: {k562_mask.shape}, adata shape: {k562_adata.shape}')

## Filter for control cells and check shape
k562_ctrl_adata = k562_adata[k562_adata.obs['perturbation'] == 'control', :]

print(f'adata shape: {k562_ctrl_adata.shape}')

#### Generate embeddings for control cells

##### Preprocess datasets

In [6]:
def gf_preprocess_replogle(data_directory, output_directory,loom_out_dir):
    
    adata = sc.read_h5ad(data_directory)
    
    print(f'adata shape: {adata.shape}')

    ## Filter for control cells and check shape
    ctrl_adata = adata[adata.obs['perturbation'] == 'control', :]

    print(f'ctrl adata shape: {ctrl_adata.shape}')
    
    #if 'filter_pass' not in ctrl_adata.obs:
     #   ctrl_adata.obs['filter_pass'] = 1

    if 'ensembl_id' not in ctrl_adata.var:
    ## Rename columns for tokenizer to function correctly
        ctrl_adata.var['ensembl_id'] = ctrl_adata.var_names
    
    if 'ncounts' in ctrl_adata.var and 'ncounts' in ctrl_adata.obs:
        #ctrl_adata.var.rename(columns={'ncounts': 'n_counts'}, inplace=True)
        ctrl_adata.obs.rename(columns={'ncounts': 'n_counts'}, inplace=True)
    
    else: 
        ctrl_adata.obs.rename(columns={'read_count': 'n_counts'}, inplace=True)
    
    ctrl_adata.write_h5ad(output_directory)
    ctrl_adata.write_loom(loom_out_dir)
    
    print(f'saved ctrl adata to {output_directory}')
    
    return ctrl_adata

In [7]:
rpe1_ctrl_adata = gf_preprocess_replogle(f'{raw_expr_path}/replogle_rpe1/replogle_rpe1_raw_counts.h5ad', f'{raw_expr_path}/tokenizer_input/ctrl_replogle_rpe1_raw_counts.h5ad', f'{raw_expr_path}/tokenizer_input/ctrl_replogle_rpe1_raw_counts.loom')
k562_ctrl_adata = gf_preprocess_replogle(f'{raw_expr_path}/replogle_k562/replogle_k562_raw_counts.h5ad', f'{raw_expr_path}/tokenizer_input/ctrl_replogle_k562_raw_counts.h5ad', f'{raw_expr_path}/tokenizer_input/ctrl_replogle_k562_raw_counts.loom')

adata shape: (247914, 8749)
ctrl adata shape: (11485, 8749)
saved ctrl adata to /data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/ctrl_replogle_rpe1_raw_counts.h5ad
adata shape: (310385, 8563)
ctrl adata shape: (10691, 8563)
saved ctrl adata to /data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/ctrl_replogle_k562_raw_counts.h5ad


##### Tokenization

In [ ]:
### FROM GENEFORMER BUT CHANGED HOW FILE IS LOADED (works on AnnData obj rather than file)

def gf_tokenize_anndata_replogle(adata, custom_attr_name_dict, genelist_dict, 
                        gene_median_dict, gene_token_dict, chunk_size = 512, target_sum = 10_000):
    #adata = ad.read(adata_path, backed="r")

    if custom_attr_name_dict is not None:
        file_cell_metadata = {
            attr_key: [] for attr_key in custom_attr_name_dict.keys()
        }

    coding_miRNA_loc = np.where(
        [genelist_dict.get(i, False) for i in adata.var["ensembl_id"]]
    )[0]
    norm_factor_vector = np.array(
        [
            gene_median_dict[i]
            for i in adata.var["ensembl_id"][coding_miRNA_loc]
        ]
    )
    coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]
    coding_miRNA_tokens = np.array(
        [gene_token_dict[i] for i in coding_miRNA_ids]
    )

    try:
        _ = adata.obs["filter_pass"]
    except KeyError:
        var_exists = False
    else:
        var_exists = True

    if var_exists:
        filter_pass_loc = np.where([i == 1 for i in adata.obs["filter_pass"]])[0]
    elif not var_exists:
        print(
            f"{adata_file_path} has no column attribute 'filter_pass'; tokenizing all cells."
        )
        filter_pass_loc = np.array([i for i in range(adata.shape[0])])

    tokenized_cells = []

    for i in range(0, len(filter_pass_loc), chunk_size):
        idx = filter_pass_loc[i : i + chunk_size]

        n_counts = adata[idx].obs["n_counts"].values[:, None]
        X_view = adata[idx, coding_miRNA_loc].X
        X_norm = X_view / n_counts * target_sum / norm_factor_vector
        X_norm = sp.csr_matrix(X_norm)

        tokenized_cells += [
            rank_genes(X_norm[i].data, coding_miRNA_tokens[X_norm[i].indices])
            for i in range(X_norm.shape[0])
        ]

        # add custom attributes for subview to dict
        if custom_attr_name_dict is not None:
            for k in file_cell_metadata.keys():
                file_cell_metadata[k] += adata[idx].obs[k].tolist()
        else:
            file_cell_metadata = None

    return tokenized_cells, file_cell_metadata

def rank_genes(gene_vector, gene_tokens):
    """
    Rank gene expression vector.
    """
    # sort by median-scaled gene values
    sorted_indices = np.argsort(-gene_vector)
    return gene_tokens[sorted_indices]


In [ ]:
def gf_tokenizer_replogle(custom_attr_name_dict, adata, genelist_dict, 
                          gene_median_dict, gene_token_dict, 
                          output_path, chunk_size = 512, target_sum = 10_000):
    
    tk = TranscriptomeTokenizer(custom_attr_name_dict, nproc=16)

    tokenized_cells, cell_metadata = gf_tokenize_anndata_replogle(adata, 
                                                                  custom_attr_name_dict, 
                                                                  genelist_dict, 
                                                                  gene_median_dict, 
                                                                  gene_token_dict,
                                                                  chunk_size = 512, 
                                                                  target_sum = 10_000)

    tokenized_dataset = tk.create_dataset(tokenized_cells, cell_metadata)

    tokenized_dataset.save_to_disk(output_path)

    print(f'Saved tokenized_dataset to {output_path}')
    
    return tokenized_cells, cell_metadata, tokenized_dataset

In [17]:
# load token dictionary (Ensembl IDs:token)
with open('/data/home/bty416/scFMs/bin/Geneformer/geneformer/token_dictionary.pkl', "rb") as f:
    gene_token_dictionary = pickle.load(f)

with open('/data/home/bty416/scFMs/bin/Geneformer/geneformer/gene_median_dictionary.pkl', "rb") as f:
    gene_median_dict = pickle.load(f)
    
# gene keys for full vocabulary
gene_keys = list(gene_token_dictionary.keys())

# protein-coding and miRNA gene list dictionary for selecting .loom rows for tokenization
genelist_dict = dict(zip(gene_keys, [True] * len(gene_keys)))

In [190]:
rpe1_output_dir = Path(f'{d_path}/tokenized_data/').resolve()
rpe1_prefix = "rpe1"
rpe1_output_path = str((Path(rpe1_output_dir) / rpe1_prefix).with_suffix(".dataset"))

rpe1_tokenized_cells, rpe1_cell_metadata, rpe1_tokenized_dataset = gf_tokenizer_replogle({"cell_line": "cell_type", "tissue_type": "tissue_type"}, 
                                                                                         rpe1_ctrl_adata, genelist_dict, gene_median_dict, 
                                                                                         gene_token_dict, rpe1_output_path)

/tmp/3600938.1.all.q/ipykernel_64317/1510350908.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/tmp/3600938.1.all.q/ipykernel_64317/1510350908.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


Creating dataset.


Saving the dataset (1/1 shards): 100%|██████████| 11485/11485 [00:00<00:00, 286611.06 examples/s]

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/rpe1.dataset


In [191]:
k562_output_dir = Path(f'{d_path}/tokenized_data/').resolve()
k562_prefix = "k562"
k562_output_path = str((Path(k562_output_dir) / k562_prefix).with_suffix(".dataset"))

k562_tokenized_cells, k562_cell_metadata, k562_tokenized_dataset = gf_tokenizer_replogle({"cell_line": "cell_type", "tissue_type": "tissue_type"}, 
                                                                                         k562_ctrl_adata, genelist_dict, gene_median_dict, 
                                                                                         gene_token_dict, k562_output_path)

/tmp/3600938.1.all.q/ipykernel_64317/1510350908.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/tmp/3600938.1.all.q/ipykernel_64317/1510350908.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


Creating dataset.


Saving the dataset (1/1 shards): 100%|██████████| 10691/10691 [00:00<00:00, 297413.32 examples/s]

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/k562.dataset


##### Embedding extraction

In [192]:
rpe1_ctrl_cell_embex = gf_extract_ctrl_embs(dataset='rpe1')
print(f'AnnData shape: {rpe1_ctrl_adata.shape}, Embedding shape: {rpe1_ctrl_cell_embex.shape}')

100%|██████████| 180/180 [00:39<00:00,  4.52it/s]


In [196]:
k562_ctrl_cell_embex = gf_extract_ctrl_embs(dataset='k562')
print(f'AnnData shape: {k562_ctrl_adata.shape}, Embedding shape: {k562_ctrl_cell_embex.shape}')

100%|██████████| 168/168 [00:36<00:00,  4.59it/s]


AnnData shape: (10691, 8563), Embedding shape: (10691, 256)


***

#### Perturbation data
##### RPE1


In [3]:
## Load data
with open(f'{raw_expr_path}/replogle_rpe1/all_perts.pkl', 'rb') as f:
    rpe1_all_perts = pkl.load(f)
    
len(rpe1_all_perts)

## Load files for RPE1 data, including mask and check shape

with open(f'{raw_expr_path}/replogle_rpe1_mask_df.pkl', 'rb') as f:
    rpe1_mask = pkl.load(f)

In [8]:
## Find perturbations in control data
rpe1_perts = (set(rpe1_ctrl_adata.var_names).intersection(rpe1_all_perts))
len(rpe1_perts)

2106

In [23]:
## Find non expressed genes
rpe1_non_exp_gene = rpe1_mask.columns[rpe1_mask.sum() == 0]

In [20]:
rpe1_pert_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/replogle_rpe1'

prep_pert_data(rpe1_perts, rpe1_mask, rpe1_ctrl_adata, rpe1_pert_path)

  9%|▊         | 180/2106 [00:00<00:02, 901.13it/s]

CYREN adata already prepared.
WDFY3 adata already prepared.
KPNA6 adata already prepared.
NUP133 adata already prepared.
MRPL33 adata already prepared.
RPL32 adata already prepared.
SKA1 adata already prepared.
UQCRQ adata already prepared.
MRPS24 adata already prepared.
UTP25 adata already prepared.
RMI1 adata already prepared.
MPG adata already prepared.
INTS13 adata already prepared.
EIF4A3 adata already prepared.
SPC24 adata already prepared.
ANLN adata already prepared.
SAE1 adata already prepared.
PPP1CA adata already prepared.
ERCC2 adata already prepared.
DOLK adata already prepared.
ORC6 adata already prepared.
NOC2L adata already prepared.
PSTK adata already prepared.
NFATC2IP adata already prepared.
H3F3A adata already prepared.
WEE1 adata already prepared.
YY1 adata already prepared.
MBTPS2 adata already prepared.
NDUFB4 adata already prepared.
EP400 adata already prepared.
FDPS adata already prepared.
SDHC adata already prepared.
CCT5 adata already prepared.
NRDE2 adata al

 17%|█▋        | 366/2106 [00:00<00:01, 917.22it/s]

AP2S1 adata already prepared.
PTK2 adata already prepared.
DCTN3 adata already prepared.
EIF3I adata already prepared.
POLR3D adata already prepared.
EXOSC8 adata already prepared.
PKM adata already prepared.
ADRM1 adata already prepared.
TFPT adata already prepared.
C9orf78 adata already prepared.
NOL8 adata already prepared.
MED4 adata already prepared.
YPEL5 adata already prepared.
GEMIN4 adata already prepared.
IMP4 adata already prepared.
PSMB2 adata already prepared.
MRPL10 adata already prepared.
CRCP adata already prepared.
NBEAL1 adata already prepared.
PSMA2 adata already prepared.
PSMD9 adata already prepared.
BRF1 adata already prepared.
CHMP2A adata already prepared.
ANKS6 adata already prepared.
INO80D adata already prepared.
RBM12 adata already prepared.
NISCH adata already prepared.
KIAA1143 adata already prepared.
INTS3 adata already prepared.
SNRPB adata already prepared.
EIF6 adata already prepared.
GNL3 adata already prepared.
PSMG4 adata already prepared.
TUBG1 ada

 26%|██▌       | 551/2106 [00:00<00:01, 919.95it/s]

...

SEC62 adata already prepared.
RNF40 adata already prepared.
BUB1 adata already prepared.
UNC50 adata already prepared.
CWC15 adata already prepared.
SRPRB adata already prepared.
BRK1 adata already prepared.
CUL2 adata already prepared.
BCAR1 adata already prepared.
MED11 adata already prepared.
POLR2C adata already prepared.
TERF2 adata already prepared.
TUFM adata already prepared.
ATP5PO adata already prepared.
SUPT16H adata already prepared.
NUP88 adata already prepared.
BPTF adata already prepared.
FNTA adata already prepared.
BRIP1 adata already prepared.
SP2 adata already prepared.
RAB18 adata already prepared.
PMPCB adata already prepared.
KRR1 adata already prepared.
RPS3 adata already prepared.
RPA2 adata already prepared.
CYCS adata already prepared.
KATNB1 adata already prepared.
XRN2 adata already prepared.
NSA2 adata already prepared.
LSM2 adata already prepared.
UTP3 adata already prepared.
TWSG1 adata already prepared.
DKC1 adata already prepared.
FARS2 adata already pr

 88%|████████▊ | 1844/2106 [00:01<00:00, 938.84it/s]

SUPT20H adata already prepared.
NAA10 adata already prepared.
TRAPPC1 adata already prepared.
NCAPD3 adata already prepared.
EIF1 adata already prepared.
CHORDC1 adata already prepared.
DRG1 adata already prepared.
EEF1A1 adata already prepared.
ZNF706 adata already prepared.
ATP5F1C adata already prepared.
SFPQ adata already prepared.
C5orf30 adata already prepared.
RPP14 adata already prepared.
SF3A3 adata already prepared.
DDX19A adata already prepared.
PSMG2 adata already prepared.
SRSF6 adata already prepared.
COPG1 adata already prepared.
SF3B3 adata already prepared.
SMC5 adata already prepared.
GEMIN5 adata already prepared.
NPM3 adata already prepared.
VHL adata already prepared.
LRR1 adata already prepared.
SNAPC3 adata already prepared.
BTF3L4 adata already prepared.
PNO1 adata already prepared.
ECT2 adata already prepared.
POLR3A adata already prepared.
PSMG3 adata already prepared.
SRP54 adata already prepared.
SCFD1 adata already prepared.
MRPS5 adata already prepared.
BR

100%|██████████| 2106/2106 [00:02<00:00, 951.25it/s]

SEC61B adata already prepared.
GTF2A1 adata already prepared.
RPS6 adata already prepared.
HMGCS1 adata already prepared.
IARS adata already prepared.
RANGAP1 adata already prepared.
POLA2 adata already prepared.
MRPS21 adata already prepared.
PGK1 adata already prepared.
TBPL1 adata already prepared.
ELP3 adata already prepared.
ALYREF adata already prepared.
BUD13 adata already prepared.
DNMT1 adata already prepared.
IFITM2 adata already prepared.
BUD23 adata already prepared.
THOC6 adata already prepared.
DYNLL1 adata already prepared.
PSMB3 adata already prepared.
SNRNP25 adata already prepared.
PIGH adata already prepared.
UBE2I adata already prepared.
RPL23A adata already prepared.
CHMP6 adata already prepared.
CLPB adata already prepared.
PPIH adata already prepared.
RNF4 adata already prepared.
TFIP11 adata already prepared.
MRPS9 adata already prepared.
SAMM50 adata already prepared.
SRCAP adata already prepared.
USP10 adata already prepared.
NDC80 adata already prepared.
NMT1

In [10]:
def tokenize_replogle_pert_data(all_perts, non_exp_genes, input_dir, output_dir, 
                                genelist_dict: dict, gene_median_dict: dict, gene_token_dict: dict):
        
    for pert in tqdm(all_perts):
        
        if pert in non_exp_genes:
            pass
        
        else:
            in_dir = f'{input_dir}/{pert}_slice.h5ad'
            adata = sc.read_h5ad(in_dir)

            prefix = f'{pert}'
            out_path = (Path(output_dir) / prefix).with_suffix(".dataset")

            if out_path.is_dir():
                print(f'{out_path} already exists {pert} adata already tokenized.')
            
            else: 
                tokenized = gf_tokenizer_replogle({"cell_line": "cell_type", "tissue_type": "tissue_type"}, 
                                                   adata, genelist_dict, gene_median_dict, 
                                                   gene_token_dict, str(out_path))

In [24]:
# load token dictionary (Ensembl IDs:token)
with open('/data/home/bty416/scFMs/bin/Geneformer/geneformer/token_dictionary.pkl', "rb") as f:
    gene_token_dictionary = pickle.load(f)

with open('/data/home/bty416/scFMs/bin/Geneformer/geneformer/gene_median_dictionary.pkl', "rb") as f:
    gene_median_dict = pickle.load(f)
    
# gene keys for full vocabulary
gene_keys = list(gene_token_dictionary.keys())

# protein-coding and miRNA gene list dictionary for selecting .loom rows for tokenization
genelist_dict = dict(zip(gene_keys, [True] * len(gene_keys)))

In [27]:
rpe1_pert_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/replogle_rpe1'
rpe1_tokenized_dir = '/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert'

rpe1_non_exp_gene = rpe1_mask.columns[rpe1_mask.sum() == 0]

tokenize_replogle_pert_data(rpe1_perts, rpe1_non_exp_gene, rpe1_pert_path, rpe1_tokenized_dir,
                           genelist_dict, gene_median_dict, gene_token_dictionary)

  0%|          | 2/2106 [00:00<03:14, 10.81it/s]

/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/CYREN.dataset already exists CYREN adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/WDFY3.dataset already exists WDFY3 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/KPNA6.dataset already exists KPNA6 adata already tokenized.


  0%|          | 6/2106 [00:00<03:05, 11.35it/s]

/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/NUP133.dataset already exists NUP133 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/MRPL33.dataset already exists MRPL33 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/RPL32.dataset already exists RPL32 adata already tokenized.


  0%|          | 8/2106 [00:00<02:55, 11.97it/s]

...

/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/DHX29.dataset already exists DHX29 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/SHOC2.dataset already exists SHOC2 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/CWC22.dataset already exists CWC22 adata already tokenized.


100%|█████████▉| 2105/2106 [1:20:45<00:00,  2.13it/s]

/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/MRPL21.dataset already exists MRPL21 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/SRRM2.dataset already exists SRRM2 adata already tokenized.
/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/PTPMT1.dataset already exists PTPMT1 adata already tokenized.


100%|██████████| 2106/2106 [1:20:45<00:00,  2.30s/it]

/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert/EIF3B.dataset already exists EIF3B adata already tokenized.


#### Generate embeddings

In [34]:
def embed_pert_data(all_perts, all_perts_embex, non_exp_genes, token_dir, output_dir, 
                    emb_mode: str = 'cell', batch_size: int = 64, dataset: str = 'rpe1'):
    
    for pert in all_perts:
        
        if pert in non_exp_genes:
            pass
        
        elif pert in all_perts_embex:
            print(f'Embedding for {pert} already added to dict')
            
        elif Path(f"{output_dir}/{pert}_pert_{emb_mode}.csv").is_file():
            print(f'Embedding for {pert} already generated. Adding to dict ...')
            emb = pd.read_csv(f"{output_dir}/{pert}_pert_{emb_mode}.csv", index_col=0)
            all_perts_embex[pert] = emb
                             
        else:
            try:
                # initiate EmbExtractor
                embex = EmbExtractor(model_type="Pretrained",
                                     num_classes=0,
                                     emb_mode=emb_mode,
                                     emb_layer=0,
                                     max_ncells=20000,
                                     forward_batch_size=batch_size,
                                     nproc=16)

                # extracts embedding from input data
                # input data is tokenized rank value encodings generated by Geneformer tokenizer (see tokenizing_scRNAseq_data.ipynb)
                # example dataset: https://huggingface.co/datasets/ctheodoris/Genecorpus-30M/tree/main/example_input_files/cell_classification/disease_classification/human_dcm_hcm_nf.dataset
                embs = embex.extract_embs("../bin/Geneformer",
                                          f'{token_dir}/{pert}.dataset',
                                          output_dir,
                                          f"{pert}_pert_{emb_mode}")

                all_perts_embex[pert] = embs
            
            except FileNotFoundError:
                print(f'{pert} file not found')
                pass
    
    with gzip.open(f"{d_path}/embeddings/{dataset}_perts_{emb_mode}.pkl.gz", 'wb') as f:
        
        pkl.dump(all_perts_embex, f)
        
    print(f'all_perts_embex saved to {d_path}/embeddings/{dataset}_perts_{emb_mode}.pkl.gz')
        
    return all_perts_embex

In [38]:
#rpe1_all_perts_embex = {}
rpe1_non_exp_gene = rpe1_mask.columns[rpe1_mask.sum() == 0]

rpe1_tokenized_dir = '/data/scratch/bty416/scFMs/data/tokenized_data/rpe1_pert'
rpe1_out_dir = f"{d_path}/embeddings/perts/rpe1"

rpe1_all_perts_embex = embed_pert_data(rpe1_perts, rpe1_all_perts_embex, rpe1_non_exp_gene, 
                                       rpe1_tokenized_dir, rpe1_out_dir,dataset='rpe1')

Embedding for RPS27A already generated. Adding to dict ...
Embedding for UTP15 already generated. Adding to dict ...
Embedding for NEDD1 already generated. Adding to dict ...
Embedding for PFDN5 already generated. Adding to dict ...
Embedding for TRMT10C already generated. Adding to dict ...
Embedding for PSMB1 already generated. Adding to dict ...
Embedding for PSMC6 already generated. Adding to dict ...
Embedding for RPS9 already generated. Adding to dict ...
Embedding for CHMP2A already generated. Adding to dict ...
Embedding for BOP1 already generated. Adding to dict ...
Embedding for ERAL1 already generated. Adding to dict ...
Embedding for ACIN1 already generated. Adding to dict ...
Embedding for INO80E already generated. Adding to dict ...
Embedding for CEP97 already generated. Adding to dict ...
Embedding for C7orf26 already generated. Adding to dict ...
Embedding for SYF2 already generated. Adding to dict ...
Embedding for SPCS2 already generated. Adding to dict ...
Embedding 

In [39]:
len(rpe1_all_perts_embex)

2105

In [40]:
for emb in rpe1_all_perts_embex.values():
    print(emb.shape)

(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)

#### K562

In [41]:
## Load data
with open(f'{raw_expr_path}/replogle_k562/all_perts.pkl', 'rb') as f:
    k562_all_perts = pkl.load(f)
    
print(len(k562_all_perts))

## Load files for K562 data, including mask and check shape

with open(f'{raw_expr_path}/replogle_k562_mask_df.pkl', 'rb') as f:
    k562_mask = pkl.load(f)
   

1866


In [42]:
## Find perturbations in control data
k562_perts = (set(k562_ctrl_adata.var_names).intersection(k562_all_perts))
len(k562_perts)

1866

In [43]:
## Find non expressed genes
k562_non_exp_gene = k562_mask.columns[k562_mask.sum() == 0]

In [46]:
k562_pert_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/replogle_k562'

prep_pert_data(k562_perts, k562_mask, k562_ctrl_adata, k562_pert_path)

 12%|█▏        | 231/1866 [00:00<00:01, 1160.25it/s]

RPS27A adata already prepared.
UTP15 adata already prepared.
NEDD1 adata already prepared.
PFDN5 adata already prepared.
TRMT10C adata already prepared.
PSMB1 adata already prepared.
PSMC6 adata already prepared.
RPS9 adata already prepared.
CHMP2A adata already prepared.
ERAL1 adata already prepared.
BOP1 adata already prepared.
ACIN1 adata already prepared.
CEP97 adata already prepared.
C7orf26 adata already prepared.
SYF2 adata already prepared.
RNF123 adata already prepared.
SPCS2 adata already prepared.
H2AFX adata already prepared.
URB1 adata already prepared.
EIF3D adata already prepared.
SRCAP adata already prepared.
COPB1 adata already prepared.
TFAM adata already prepared.
GRSF1 adata already prepared.
MAX adata already prepared.
DSN1 adata already prepared.
UTP6 adata already prepared.
RNF4 adata already prepared.
HNRNPH1 adata already prepared.
TUBG1 adata already prepared.
VEZT adata already prepared.
MCM4 adata already prepared.
NSMCE2 adata already prepared.
BRD4 adata a

 25%|██▌       | 474/1866 [00:00<00:01, 1192.11it/s]

PPME1 adata already prepared.
MRPL43 adata already prepared.
SRRM1 adata already prepared.
PGPEP1 adata already prepared.
TSEN34 adata already prepared.
RPL34 adata already prepared.
RAB6A adata already prepared.
CEP68 adata already prepared.
INTS6 adata already prepared.
TACC3 adata already prepared.
SMNDC1 adata already prepared.
VCP adata already prepared.
PABPC1 adata already prepared.
COASY adata already prepared.
RNPS1 adata already prepared.
TAMM41 adata already prepared.
C17orf58 adata already prepared.
VPS33A adata already prepared.
CCNH adata already prepared.
RAD17 adata already prepared.
GTF2E2 adata already prepared.
AP2M1 adata already prepared.
TRMT5 adata already prepared.
DOHH adata already prepared.
PSMB3 adata already prepared.
CDC6 adata already prepared.
MRPS10 adata already prepared.
TBCB adata already prepared.
ZNF100 adata already prepared.
POT1 adata already prepared.
CDCA5 adata already prepared.
GTF2H2C adata already prepared.
BRK1 adata already prepared.
TXN

 39%|███▊      | 719/1866 [00:00<00:00, 1202.32it/s]

...

NUP160 adata already prepared.
EGLN2 adata already prepared.
CEBPZ adata already prepared.
EXOSC7 adata already prepared.
PTMA adata already prepared.
DPM2 adata already prepared.
RPE adata already prepared.
LUC7L3 adata already prepared.
THOC5 adata already prepared.
HSP90B1 adata already prepared.
CWF19L2 adata already prepared.
NUF2 adata already prepared.
WBP1 adata already prepared.
CHEK1 adata already prepared.
ZCRB1 adata already prepared.
MED10 adata already prepared.
RPA2 adata already prepared.
CCT8 adata already prepared.
PARS2 adata already prepared.
TIMM13 adata already prepared.
HOXC10 adata already prepared.
ACTR6 adata already prepared.
UBTF adata already prepared.
PRKRIP1 adata already prepared.
DCTN3 adata already prepared.
XRN2 adata already prepared.
NPM3 adata already prepared.
SMARCB1 adata already prepared.
SDHAF2 adata already prepared.
RPL7L1 adata already prepared.
PSMD9 adata already prepared.
CENPH adata already prepared.
PSMD7 adata already prepared.
SNUPN 

 92%|█████████▏| 1715/1866 [00:01<00:00, 1225.87it/s]

VHL adata already prepared.
TMSB10 adata already prepared.
NSA2 adata already prepared.
RPS14 adata already prepared.
RPL30 adata already prepared.
TEFM adata already prepared.
SLC25A3 adata already prepared.
PWP1 adata already prepared.
EIF3G adata already prepared.
ARID3A adata already prepared.
MED27 adata already prepared.
DNAJC8 adata already prepared.
C19orf25 adata already prepared.
FAU adata already prepared.
DHFR adata already prepared.
SNRPD3 adata already prepared.
RACGAP1 adata already prepared.
CIAO1 adata already prepared.
HTATSF1 adata already prepared.
PFDN2 adata already prepared.
SMARCE1 adata already prepared.
TRIAP1 adata already prepared.
PRPF6 adata already prepared.
MRPS35 adata already prepared.
UBE2N adata already prepared.
DNMT1 adata already prepared.
COG3 adata already prepared.
CDC23 adata already prepared.
SF3A2 adata already prepared.
NXF1 adata already prepared.
URM1 adata already prepared.
PTBP1 adata already prepared.
CDC26 adata already prepared.
EIF3

100%|██████████| 1866/1866 [00:01<00:00, 1216.52it/s]

CCNB1 adata already prepared.
RPS3 adata already prepared.
RPS4X adata already prepared.
SAMM50 adata already prepared.
ZNF317 adata already prepared.
SLC39A9 adata already prepared.
PGD adata already prepared.
ACTB adata already prepared.
TCOF1 adata already prepared.
BRIP1 adata already prepared.
SFSWAP adata already prepared.
PNO1 adata already prepared.
DNAJC9 adata already prepared.
ABHD11 adata already prepared.
FAM32A adata already prepared.
CCT3 adata already prepared.
NAA10 adata already prepared.
TAF8 adata already prepared.
POLR3H adata already prepared.
CPSF6 adata already prepared.
OGT adata already prepared.
FAM207A adata already prepared.
NDUFB6 adata already prepared.
MYCBP adata already prepared.
SART3 adata already prepared.
RBX1 adata already prepared.
EP400 adata already prepared.
POLR2E adata already prepared.
MCMBP adata already prepared.
SRSF6 adata already prepared.
INTS7 adata already prepared.
CHD4 adata already prepared.
DENR adata already prepared.
GIT2 adat

In [ ]:
# load token dictionary (Ensembl IDs:token)
with open('/data/home/bty416/scFMs/bin/Geneformer/geneformer/token_dictionary.pkl', "rb") as f:
    gene_token_dictionary = pickle.load(f)

with open('/data/home/bty416/scFMs/bin/Geneformer/geneformer/gene_median_dictionary.pkl', "rb") as f:
    gene_median_dict = pickle.load(f)
    
# gene keys for full vocabulary
gene_keys = list(gene_token_dictionary.keys())

# protein-coding and miRNA gene list dictionary for selecting .loom rows for tokenization
genelist_dict = dict(zip(gene_keys, [True] * len(gene_keys)))

In [32]:
k562_pert_path = '/data/scratch/bty416/scFMs/data/raw_expression_counts/tokenizer_input/perts/replogle_k562'
k562_tokenized_dir = '/data/scratch/bty416/scFMs/data/tokenized_data/k562_pert'

k562_non_exp_gene = k562_mask.columns[k562_mask.sum() == 0]

tokenize_replogle_pert_data(k562_perts, k562_non_exp_gene, k562_pert_path, k562_tokenized_dir,
                           genelist_dict, gene_median_dict, gene_token_dictionary)

  0%|          | 0/1866 [00:00<?, ?it/s]/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


Creating dataset.



Map (num_proc=16): 100%|██████████| 500/500 [00:22<00:00, 21.78 examples/s]

  0%|          | 1/1866 [00:25<13:18:48, 25.70s/it]/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/k562_pert/KPNA6.dataset
Creating dataset.



Map (num_proc=16): 100%|██████████| 500/500 [00:20<00:00, 24.92 examples/s]

  0%|          | 2/1866 [00:48<12:25:04, 23.98s/it]/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


...

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/k562_pert/PTPMT1.dataset
Creating dataset.



Map (num_proc=16): 100%|██████████| 500/500 [00:20<00:00, 24.83 examples/s]

100%|█████████▉| 1865/1866 [11:51:26<00:23, 23.11s/it]/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  for i in adata.var["ensembl_id"][coding_miRNA_loc]
/tmp/3602758.1.all.q/ipykernel_2280/4280839296.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  coding_miRNA_ids = adata.var["ensembl_id"][coding_miRNA_loc]


Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/k562_pert/EIF3B.dataset
Creating dataset.



Map (num_proc=16): 100%|██████████| 500/500 [00:19<00:00, 25.64 examples/s]

100%|██████████| 1866/1866 [11:51:48<00:00, 22.89s/it]

Saved tokenized_dataset to /data/scratch/bty416/scFMs/data/tokenized_data/k562_pert/WDR24.dataset


In [ ]:
k562_all_perts_embex = {}
k562_non_exp_gene = k562_mask.columns[k562_mask.sum() == 0]

k562_tokenized_dir = '/data/scratch/bty416/scFMs/data/tokenized_data/k562_pert'
k562_out_dir = f"{d_path}/embeddings/perts/k562"

k562_all_perts_embex = embed_pert_data(k562_perts, k562_all_perts_embex, k562_non_exp_gene, 
                                       k562_tokenized_dir, k562_out_dir,dataset='k562')

Embedding for RPS27A already generated. Adding to dict ...
Embedding for UTP15 already generated. Adding to dict ...
Embedding for NEDD1 already generated. Adding to dict ...
Embedding for PFDN5 already generated. Adding to dict ...
Embedding for TRMT10C already generated. Adding to dict ...
Embedding for PSMB1 already generated. Adding to dict ...
Embedding for PSMC6 already generated. Adding to dict ...
Embedding for RPS9 already generated. Adding to dict ...
Embedding for CHMP2A already generated. Adding to dict ...
Embedding for ERAL1 already generated. Adding to dict ...
Embedding for BOP1 already generated. Adding to dict ...
Embedding for ACIN1 already generated. Adding to dict ...
Embedding for CEP97 already generated. Adding to dict ...
Embedding for C7orf26 already generated. Adding to dict ...
Embedding for SYF2 already generated. Adding to dict ...
Embedding for RNF123 already generated. Adding to dict ...
Embedding for SPCS2 already generated. Adding to dict ...
Embedding 

In [48]:
len(k562_all_perts_embex)

1866

In [62]:
for emb in k562_all_perts_embex.values():
    print(emb.shape) 

(500, 256)
(3, 256)
(500, 256)
(94, 256)
(500, 256)
(92, 256)
(5, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(111, 256)
(500, 256)
(500, 256)
(8, 256)
(500, 256)
(334, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(292, 256)
(500, 256)
(500, 256)
(500, 256)
(7, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(425, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(158, 256)
(500, 256)
(416, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(78, 256)
(500, 256)
(500, 256)
(43, 256)
(500, 256)
(500, 256)
(271, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(500, 256)
(104, 256)
(10, 256)
(27, 256)
(500, 256)
(47, 256)
(38, 256)
(500, 256)
(500, 256)
(189